In [6]:
import csv
import itertools
import operator
import numpy as np
import nltk
import sys
from datetime import datetime
from utils import *

import matplotlib.pyplot as plt
%matplotlib inline

In [18]:
# Download NLTK model data (you need to do this once)
nltk.download("book")

[nltk_data] Downloading collection 'book'
[nltk_data]    | 
[nltk_data]    | Downloading package abc to
[nltk_data]    |     C:\Users\PXS180040\AppData\Roaming\nltk_data...
[nltk_data]    |   Package abc is already up-to-date!
[nltk_data]    | Downloading package brown to
[nltk_data]    |     C:\Users\PXS180040\AppData\Roaming\nltk_data...
[nltk_data]    |   Package brown is already up-to-date!
[nltk_data]    | Downloading package chat80 to
[nltk_data]    |     C:\Users\PXS180040\AppData\Roaming\nltk_data...
[nltk_data]    |   Package chat80 is already up-to-date!
[nltk_data]    | Downloading package cmudict to
[nltk_data]    |     C:\Users\PXS180040\AppData\Roaming\nltk_data...
[nltk_data]    |   Package cmudict is already up-to-date!
[nltk_data]    | Downloading package conll2000 to
[nltk_data]    |     C:\Users\PXS180040\AppData\Roaming\nltk_data...
[nltk_data]    |   Package conll2000 is already up-to-date!
[nltk_data]    | Downloading package conll2002 to
[nltk_data]    |     C:\U

True

### Data Preprocessing

In [22]:
vocabulary_size = 8000
unknown_token = "UNKNOWN_TOKEN"
sentence_start_token = "SENTENCE_START"
sentence_end_token = "SENTENCE_END"

# Read the data and append SENTENCE_START and SENTENCE_END tokens
print ("Reading CSV file...")
with open('data/reddit-comments-2015-08.csv', 'r',encoding="utf8") as f:
    reader = csv.reader(f, skipinitialspace=True)
    for x in reader:
        print(nltk.sent_tokenize(x[0].lower()))
             

Reading CSV file...
['body']
["i joined a new league this year and they have different scoring rules than i'm used to.", "it's a slight ppr league- .2 ppr.", 'standard besides 1 points for 15 yards receiving, .2 points per completion, 6 points per td thrown, and some bonuses for rec/rush/pass yardage.', 'my question is, is it wildly clear that qb has the highest potential for points?', 'i put in the rules at a ranking site and noticed that top qbs had 300 points more than the top rb/wr.', 'would it be dumb not to grab a qb in the first round?']
['in your scenario, a person could just not run the mandatory background check on the buyer and still sell the gun to the felon.', "there's no way to enforce it.", "an honest seller is going to not sell the gun to them when they see they're a felon on the background check.", "a dishonest seller isn't going to run the check in the first place.", 'no one is going to be honest enough to run the check, see they\'re a felon, and then all of a sudden 

["not sure if true or not, regardless it doesn't make any difference for that one guy that has the money and just puts it on an esports match.", 'i\'m sorry, but if the security mechanism is really "there has been a 2k bet" then it is retarted.', 'if anything it shows that if one guy with a 2k dollar bet can skew the odds that much, then the whole business should not exist in the first place.']
["i honestly thought souma falling asleep would hurt his dish..glad it didn't\n\noh the reactions of those megumi haters...so satisfying.", 'i almost spit out my tea when nao turned into her "white" form\n\nonly 3 episodes left..2nd season announcement or riot!']
['start with two arduino micros from a reputable seller.', "you'll want one to mess with while the other is running in production, and these little guys have enough pins on them to drive your project and more.", 'get two micro usb cables as well.', 'pick up a good digital multimeter, a spool of small electronic wire, a grab-bag of 1/8 w

['his skill set makes for a very diverse hero in terms of item builds, bots and rapiers work because of that but so does necrobook, dagon, e-blade and every other active item you can think of(not refresher).', 'i believe the most consistent build back in dota1 was midas&gt;necrobook and just push/teamfight your way to victory.']
["hardly, it's combat arms' anti-cheat.", 'so, only slightly better than what they had before.', "plus, don't even need to hack with the rampant bugs and imbalance.", "i mean, it's a beta but they're clearly cashing in on selling new characters when they're op."]
['apparently this is already a thing called twincharging.', 'some of the volkswagen 1.4l tsi engines are twincharged.', 'disadvantage seems to be that these are expensive to make and too complex to maintain.', 'twin turbo and twin scroll turbo systems seem to do a similar job while keeping the system less complex.']
['1) there is no such thing as porn addiction.', "it's a fable created by religion.", "

['what is wrong with you?', '8/10 is a great score.', "don't get mad just because they delivered a lower score than your circlejerk allows.", 'the world of witcher 3 is racist and sexist, and i can see people having an issue with that.']
['according to this it is: http://blog.us.playstation.com/2015/08/25/mega-man-legacy-collection-out-today-on-ps4/\n\nthis link seems to work: https://store.playstation.com/#!/en-us/games/mega-man-legacy-collection/cid=up0102-cusa02516_00-megamanlegacy000\n\nalso this is the eu link: https://store.playstation.com/#!/en-au/games/mega-man-legacy-collection/cid=ep0102-cusa02521_00-megamanlegacy000']
["okay i don't know what ahppened but when i clicked on my inbox all i saw was this\n\n&gt;okay so what happens now that i've proven you to be a liar?", "and the quote that was above it ,i then went looking for that comment again and as that actual comment obviously had lots more written after it i didn't even bother to check if it was that comment.", "any way 

['doo *dodododo* ...\n\ndoo *dodododo* ...\n\n|\n\n  dooo*dododo* *dodododo* *dodododo* *dodododo*\n\n  dooo*dododo* *dodododo* *dodododo* *dodododo*\n\n  **doo** *dododododo* *dododododododo*\n\n  *dododododododo* *dododododododo*\n\n  **do do do do do** *dodododo* **do do do do** *dododo do*\n\n|\n\ndoo\n\n**dodododo**\n\n**dodododo**\n\n**dodododo**']
['no advocates for anything.', 'read the rules linked in the sidebar.', 'talk about what worked for you where appropriate.', "speak fro the i.  do not preach, do not tell others what to do, do not 'advocate.'"]
['you get issued reusable ones.', 'when i got out, the double sided yellow/green ones were standard issue.', 'in addition many units try to issue out as much electronic earpro as possible.', 'related to your question, i personally reccomend surefire ep plugs as a personally bought alternative to the issued yellow/green plugs because they sit more comfortably in the ear, and fit under electronic earpro no problem.']
["i'd also li

...

['this is very fun and thank you for posting it.', "i've seen a few choices with shanks, whitebeard and kuma.", "people seem to be thinking of your own teams strength's vs what the consequences of not having choose them would be as well.", "i thought i'd make a strength list with a simple breakdown of their strength, weakness, position and \nspecific usefulness in a team.", '1. whitebeard - offensive - strongest man in the world, quake fruit and haki - whitebeard is with his fruit, haki and weapon is just a beast.', 'the war of the best showed just how strong whitebeard was and where he ranked against everyone else.', "people like to give akainu credit with beating whitebeard but his stab injury or his illness worsened by the stab caused him to be open to akainu's attack.", 'an uninjured wb would be smacking most the "brats" left and right.', "there's also the chance that his illness could momentarily cripple him leaving him or open.", 'not choosing wb could go one of two ways: bad and

['strange.', 'sounds like something is wrong with you mac if anything is freezing on a regular basis.', "sure it's old, but that doesn't sound right.", "plus chrome has the worst memory usage of the 3 so it's weird that it's not freezing.", 'sounds like just random luck.']
["for the hammerhead challenge, sjin didn't actually hit it, no one (except derpulies) did any direct damage to it, they all died instantly as soon as they got close to it, sjin (accidentally) used the aoe fire effect from the hammer to kill it.", 'as such, kim would not of been able to kill it, unless she got a bow or something.', "(i personally don't care about that win, i'm just pointing out that you're not entirely correct)"]
['thank you!', 'i may get down voted for this but imo mauls "survival" is an absolute joke.', "plus, i'm guessing he has to have at least one major organ in his lower half, he's a zabrak which is very close to human.", 'he should be dead.']
['i think some equipment is simple enough to use wi

['that hair.', "my girlfriend is mixed, half black and half white, so she has the most amazingly beautiful curls that made me stare at her in a way that i hope wasn't too creepy.", 'she said she was used to white boys from central minnesota having that kind of reaction.']
['way too much time and not enough time.', 'the change in my storage has really set me back.', 'also, i keep track of my inventory in 3 different places-bricklink, brick store (could be brick stock, i forget which one i use) and an excel spreadsheet.', 'it takes me about 25 minutes to pull the order and another 30 minutes to address my bookkeeping.', "bigger orders take longer, but as long as you have a well organized system pulling an order shouldn't take too long.", 'the bookkeeping is up to you.', 'bricklink inventory should be enough for most people, but i keep track of cost per piece, price per piece, and the different inventories.', 'as for parting out a set, takes me about two hours to do all the stuff.', "earl

["**my best expansion: wrath, but tbc is a very close second**\n\n&gt; **leveling time: wrath** \n\nit wasn't too hard, but it wasn't a breeze either.", 'mobs were still a pain to deal with, which made you think more about it.', "since leveling was a bit of a chore, even with heirlooms, you didn't have a top-level alt in every class and you had to really commit to one maybe 2 or 3 character(s)\n\n&gt; **leveling experience: mop**\n\nsay what you will about how boring and stale end-game wod is or how boring mop was at max level grinding dailies constantly....both of these expansions had awesome leveling experiences.", 'it put you directly in the middle of the action, making you a key character in it all which was nice.', 'the big reason why mop takes the cake is because it did a way better job telling the story than wod did.', "in mop there was struggle, in wod shit just sorta worked out, and you could tell the writers were beginning to run out of steam\n\n&gt; **dungeons: tbc/wrath**\n

['so there was this one time!', 'shortly after moving in together my boyfriend and i were spending our saturday unpacking.', 'i had put all the bedding stuff in a tall skinny box.', 'upon emptying out this box i decided i was going to break it down, so i went to the kitchen to grab a knife.', 'upon returning i walked up to the box and suddenly it came alive, there was a huge roar and my boyfriend popped out of the box.', "my fight or flight kicked in, turns out i'm big on flight over fight.", "i ran across the room and hid behind the bed, my boyfriend is dying of laughter, i'm dying of laughter... with a knife in my hand.", '"oh my god babe, i could have killed you."', 'then he reminded me, "you can\'t kill anyone running away."', 'dammit, he was right.']
['i just said "what the fuck" aloud as i read this, i\'m so sorry.', 'thank god you have a good friend in alice.', 'maybe try looking into lgbt support groups in your area as they might be able to offer advice or potentially counselin